# 01. Librerías y Datos

In [1]:
import numpy as np
import pandas as pd
import plotly.express as px
import yfinance as yf
from tqdm import tqdm

In [2]:
date_start= '2021-05-01'
date_end= '2024-05-01'
tickers = ["NVDA","CSCO","JNJ","JPM","BAC","GOOG","DIS","KO"]

In [3]:
df_adj_close = pd.DataFrame()
for ticker in tqdm(tickers):
    data = yf.download(ticker, start=date_start, end=date_end, progress=False)
    df_adj_close[ticker] = data['Adj Close']
df_adj_close

  0%|          | 0/8 [00:00<?, ?it/s]

100%|██████████| 8/8 [00:08<00:00,  1.01s/it]


NVDA       CSCO         JNJ         JPM        BAC  \
Date                                                                   
2021-05-03  148.078018  46.734673  152.193436  140.980637  37.636356   
2021-05-04  143.232452  46.314548  154.551697  142.929535  38.044632   
2021-05-05  144.302887  46.698139  153.906876  144.804886  38.406525   
2021-05-06  144.946609  47.894588  154.524048  147.718979  38.981834   
2021-05-07  147.833466  48.798782  155.224197  148.224579  39.139580   
...                ...        ...         ...         ...        ...   
2024-04-24  796.770020  48.349998  148.529999  193.080002  38.320000   
2024-04-25  826.320007  48.099998  146.820007  193.369995  37.910000   
2024-04-26  877.349976  47.860001  146.139999  193.490005  37.830002   
2024-04-29  877.570007  47.779999  146.820007  193.279999  37.549999   
2024-04-30  864.020020  46.980000  144.589996  191.740005  37.009998   

                  GOOG         DIS         KO  
Date                                           
2021-05-03  119.758499  184.907364  49.744427  
2021-05-04  117.712502  183.651459  49.433968  
2021-05-05  117.836998  180.920364  49.306145  
2021-05-06  119.067497  181.199448  49.799217  
2021-05-07  119.934502  184.239548  49.771812  
...                ...         ...        ...  
2024-04-24  161.100006  113.919998  61.549999  
2024-04-25  157.949997  112.769997  61.740002  
2024-04-26  173.690002  112.730003  61.740002  
2024-04-29  167.899994  112.080002  62.040001  
2024-04-30  164.639999  111.099998  61.770000  

[754 rows x 8 columns]

# 02. Exploración de datos

In [4]:
df_long= pd.DataFrame(df_adj_close.stack(0)).reset_index().rename(columns={'level_1': 'Stock', 0: 'Price'})
px.line(df_long, x='Date', y='Price', color='Stock', title='Stock Prices')

In [5]:
px.imshow(round(df_adj_close.corr(),2), color_continuous_scale='RdBu', range_color=(-1, 1),
        text_auto=True, width=600, height=600, title='Correlation of stocks')

In [6]:
df_pct_change= df_adj_close.pct_change()
df_pct_change

NVDA      CSCO       JNJ       JPM       BAC      GOOG  \
Date                                                                     
2021-05-03       NaN       NaN       NaN       NaN       NaN       NaN   
2021-05-04 -0.032723 -0.008990  0.015495  0.013824  0.010848 -0.017084   
2021-05-05  0.007473  0.008282 -0.004172  0.013121  0.009512  0.001058   
2021-05-06  0.004461  0.025621  0.004010  0.020124  0.014979  0.010442   
2021-05-07  0.019917  0.018879  0.004531  0.003423  0.004047  0.007282   
...              ...       ...       ...       ...       ...       ...   
2024-04-24 -0.033316  0.000621 -0.006887  0.004892 -0.001303  0.007379   
2024-04-25  0.037087 -0.005171 -0.011513  0.001502 -0.010699 -0.019553   
2024-04-26  0.061756 -0.004990 -0.004632  0.000621 -0.002110  0.099652   
2024-04-29  0.000251 -0.001672  0.004653 -0.001085 -0.007402 -0.033335   
2024-04-30 -0.015440 -0.016743 -0.015189 -0.007968 -0.014381 -0.019416   

                 DIS        KO  
Date                            
2021-05-03       NaN       NaN  
2021-05-04 -0.006792 -0.006241  
2021-05-05 -0.014871 -0.002586  
2021-05-06  0.001543  0.010000  
2021-05-07  0.016778 -0.000550  
...              ...       ...  
2024-04-24  0.001847  0.015007  
2024-04-25 -0.010095  0.003087  
2024-04-26 -0.000355  0.000000  
2024-04-29 -0.005766  0.004859  
2024-04-30 -0.008744 -0.004352  

[754 rows x 8 columns]

In [7]:
df_pct_change_long= pd.DataFrame(df_pct_change.stack(0)).reset_index().rename(columns={'level_1': 'Stock', 0: 'Price'})
px.histogram(df_pct_change_long, x='Price', facet_col='Stock', nbins=50, title='Daily Percentage Change in Stock Prices', facet_col_wrap=3, height=800)

# 03. Markowitz Portfolio Optimization

In [8]:
np.random.seed(1)
weights = np.random.random((len(tickers),1))
weights /= np.sum(weights)
weights

array([[1.88637233e-01],
       [3.25834172e-01],
       [5.17367162e-05],
       [1.36758203e-01],
       [6.63840874e-02],
       [4.17687720e-02],
       [8.42536138e-02],
       [1.56312182e-01]])

In [9]:
df_log_return= np.log(df_adj_close/df_adj_close.shift(1))
df_log_return

NVDA      CSCO       JNJ       JPM       BAC      GOOG  \
Date                                                                     
2021-05-03       NaN       NaN       NaN       NaN       NaN       NaN   
2021-05-04 -0.033270 -0.009030  0.015376  0.013729  0.010789 -0.017232   
2021-05-05  0.007446  0.008248 -0.004181  0.013035  0.009467  0.001057   
2021-05-06  0.004451  0.025298  0.004002  0.019924  0.014868  0.010388   
2021-05-07  0.019721  0.018703  0.004521  0.003417  0.004038  0.007255   
...              ...       ...       ...       ...       ...       ...   
2024-04-24 -0.033884  0.000621 -0.006911  0.004880 -0.001304  0.007352   
2024-04-25  0.036416 -0.005184 -0.011580  0.001501 -0.010757 -0.019747   
2024-04-26  0.059924 -0.005002 -0.004642  0.000620 -0.002112  0.094994   
2024-04-29  0.000251 -0.001673  0.004642 -0.001086 -0.007429 -0.033904   
2024-04-30 -0.015561 -0.016885 -0.015305 -0.008000 -0.014485 -0.019607   

                 DIS        KO  
Date                            
2021-05-03       NaN       NaN  
2021-05-04 -0.006815 -0.006261  
2021-05-05 -0.014983 -0.002589  
2021-05-06  0.001541  0.009951  
2021-05-07  0.016638 -0.000550  
...              ...       ...  
2024-04-24  0.001845  0.014895  
2024-04-25 -0.010146  0.003082  
2024-04-26 -0.000355  0.000000  
2024-04-29 -0.005783  0.004847  
2024-04-30 -0.008782 -0.004362  

[754 rows x 8 columns]

In [10]:
expected_return= df_log_return.mean().dot(weights)*252
expected_return

array([0.12703475])

In [11]:
expectec_volatility= np.sqrt(np.dot(weights.T, np.dot(df_log_return.cov()*252, weights)))
expectec_volatility

array([[0.2086563]])

In [12]:
sharpe_ratio= expected_return/expectec_volatility
sharpe_ratio

array([[0.60882299]])

# 04. Simulation

In [13]:
# number of simulation
n = 50_000
# n = 10

port_weights = np.zeros(shape=(n,len(df_adj_close.columns)))
port_volatility = np.zeros(n)
port_sr = np.zeros(n)
port_return = np.zeros(n)

num_securities = len(df_adj_close.columns)
# num_securities
for i in tqdm(range(n)):
    # Weight each security
    weights = np.random.random(len(tickers))
    # normalize it, so that some is one
    weights /= np.sum(weights)
    port_weights[i,:] = weights 
    #     print(f'Normalized Weights : {weights.flatten()}')

    # Expected return (weighted sum of mean returns). Mult by 252 as we always do annual calculation and year has 252 business days
    exp_ret = df_log_return.mean().dot(weights)*252 
    port_return[i] = exp_ret
#     print(f'\nExpected return is : {exp_ret[0]}')

    # Exp Volatility (Risk)
    exp_vol = np.sqrt(weights.T.dot(252*df_log_return.cov().dot(weights)))
    port_volatility[i] = exp_vol
#     print(f'\nVolatility : {exp_vol[0][0]}')

    # Sharpe ratio
    sr = exp_ret / exp_vol
    port_sr[i] = sr
#     print(f'\nSharpe ratio : {sr[0][0]}')

100%|██████████| 50000/50000 [01:14<00:00, 667.48it/s]


In [14]:
df_results= pd.DataFrame({'Return': port_return, 'Volatility': port_volatility, 'Sharpe Ratio': port_sr})
df_results

Return  Volatility  Sharpe Ratio
0      0.113805    0.185047      0.615006
1      0.088198    0.198989      0.443231
2      0.181309    0.245821      0.737564
3      0.151057    0.204457      0.738818
4      0.126084    0.225047      0.560254
...         ...         ...           ...
49995  0.160153    0.192071      0.833824
49996  0.094651    0.213533      0.443264
49997  0.003518    0.188723      0.018639
49998  0.122610    0.235767      0.520050
49999  0.137207    0.210421      0.652060

[50000 rows x 3 columns]

In [15]:
# Index of max Sharpe Ratio
max_sr = port_sr.max()
ind = port_sr.argmax()
# Return and Volatility at Max SR
max_sr_ret = port_return[ind]
max_sr_vol = port_volatility[ind]

In [16]:
fig= px.scatter(df_results, x='Volatility', y='Return', color='Sharpe Ratio', title='Portfolio Optimization', width=800, height=600)
#add the max SR point
fig.add_trace(px.scatter(x=[max_sr_vol], y=[max_sr_ret], color=[max_sr], size=[100]).data[0])
fig.show()

In [17]:
for weight, stock in zip(port_weights[ind],(df_adj_close.columns)):
    print(f'{round(weight * 100, 2)} % of {stock} should be bought.')
    
# best portfolio return
print(f'\nMarkowitz optimal portfolio return is : {round(max_sr_ret * 100, 2)}% with volatility \
{max_sr_vol}')

35.28 % of NVDA should be bought.
3.23 % of CSCO should be bought.
21.06 % of JNJ should be bought.
2.05 % of JPM should be bought.
1.01 % of BAC should be bought.
1.23 % of GOOG should be bought.
0.44 % of DIS should be bought.
35.7 % of KO should be bought.

Markowitz optimal portfolio return is : 23.32% with volatility 0.22186654397763622
